# Async mode & Python models

<div class="admonition example">
<p class="admonition-title">Example</p>
<p>The sources of this example app are available on GitHub:
<a href="https://github.com/amsdal/amsdal-travel-app/tree/async-py">Travel App Example (Py &amp; Async)</a></p>
<p>The deployed Demo Travel App is available here:
<a href="https://main-c1798f42a01b4ca8b575b6f61b13c9f6.cloud.amsdal.com/docs">Demo Travel App</a></p>
</div>

## Step 1 - Install AMSDAL

In [ ]:
!pip install "amsdal[cli]"

For more detailed installation instructions, please refer to the [Installation Guide](/docs/installation).

## Step 2 - Create an application

Let's create a new application using the `amsdal-cli` tool.

First of all we need to create an empty `temp` directory for our application. You can create it anywhere you want, we will use the `tempfile` module to create a temporary directory for our application:

In [ ]:
import os
import tempfile
from pathlib import Path

notebook_dir = os.environ.setdefault('BASE_NOTEBOOK_DIR', os.getcwd())
print('Notebook dir:', notebook_dir)
temp_dir = tempfile.TemporaryDirectory()
working_directory = Path(temp_dir.name)

print('Workdir:', working_directory)

Now, let's create a new application in the `working_directory` directory:

In [ ]:
!amsdal new --models-format py --async TravelApp {working_directory}

Note, we are using the Python format for models in this example.
It created a new directory `travel_app` with an empty AMSDAL application in our working directory.

Detailed information about the command and the files it has created can be found in
the [CLI reference](/cli/overview.md#create-application-using-cli).

We also need to install python packages from generated `requirements.txt` file:



In [ ]:
%cd {working_directory}/travel_app

!pip install -r requirements.txt

## Step 3 - Defining the models

The first of all, let’s design ERD (entity relationship diagram) for our models:

![Travel App: ERD](/media/images/dark/erd.png#only-dark)
![Travel App: ERD](/media/images/light/erd.png#only-light)

As we can see, the app will provide the ability to plan journeys, add to these journeys some people, and book
properties.

Now we can define our models’ schemas. We will use AMSDAL CLI to generate these models. Go to the `travel_app` directory and run the following commands in the
terminal:

In [ ]:
!amsdal generate model Country -attrs "name:string code:string"
!amsdal generate model Person -attrs "first_name:string last_name:string dob:string"
!amsdal generate model Property -attrs "name:string type:string address:string free_parking:boolean free_wifi:boolean photos:has-many:File"
!amsdal generate model Booking -attrs "property:belongs-to:Property date:string nights:number:default=1"
!amsdal generate model Journey -attrs "start_date:string end_date:string country:belongs-to:Country persons:has-many:Person equipment:dict:string:number bookings:has-many:Booking"

print()
print('All models generated successfully!')

Perfect, now, we have all defined models and are ready to run the local server to check it.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>You can find more details regarding the <code>amsdal generate model</code> command in
the <a href="../cli/overview.md#generate-models">CLI reference</a>.</p>
</div>

## Step 4 - Run local server

AMSDAL CLI provides the ability to run a local server to test the application.

The first time you run the commands below, e.g. `amsdal migrations new`, you need to complete the registration process. Just follow the instructions in the terminal. See details [here](/cli/overview.md#run-local-server)

When you will get credentials, set them below:

In [ ]:
# put your credentials here
AMSDAL_ACCESS_KEY_ID = ''
AMSDAL_SECRET_ACCESS_KEY = ''

import os
os.environ["AMSDAL_ACCESS_KEY_ID"] = os.getenv("AMSDAL_ACCESS_KEY_ID") or AMSDAL_ACCESS_KEY_ID
os.environ["AMSDAL_SECRET_ACCESS_KEY"] = os.getenv("AMSDAL_SECRET_ACCESS_KEY") or  AMSDAL_SECRET_ACCESS_KEY

# Verify that the environment variables are set
print('AMSDAL_ACCESS_KEY_ID:', os.environ['AMSDAL_ACCESS_KEY_ID'])
print('AMSDAL_SECRET_ACCESS_KEY:', os.environ['AMSDAL_SECRET_ACCESS_KEY'])


Let’s run it and check the result.
From the root directory of the `travel_app` run the following command in the terminal:

In [ ]:
!amsdal migrations new
!amsdal migrations apply

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>These steps must be performed each time changes are made to models (creating, deleting, modifying existing models)</p>
</div>

Now, let's run the local server using the following command:

```bash
amsdal serve
```

It will run the local API server, the Swagger documentation of it is available at this
link: [http://localhost:8080/docs](http://localhost:8080/docs)

Also, we can use the **AMSDAL Console** - the web portal that is hosted
on [https://console.amsdal.com/](https://console.amsdal.com/).

An unauthorized user cannot log in and access the data, so you need to create a new user:


In [ ]:
# put your user credentials here
AMSDAL_ADMIN_USER_EMAIL = 'admin@amsdal.com'
AMSDAL_ADMIN_USER_PASSWORD = 'DemoPassword1234!'
AUTH_JWT_KEY = 'my-secret-jwt-key'

import os
os.environ["AMSDAL_ADMIN_USER_EMAIL"] = os.getenv("AMSDAL_ADMIN_USER_EMAIL") or AMSDAL_ADMIN_USER_EMAIL
os.environ["AMSDAL_ADMIN_USER_PASSWORD"] = os.getenv("AMSDAL_ADMIN_USER_PASSWORD") or AMSDAL_ADMIN_USER_PASSWORD
os.environ["AUTH_JWT_KEY"] = os.getenv("AUTH_JWT_KEY") or AUTH_JWT_KEY

Note, that the `AUTH_JWT_KEY` is a secret key for JWT token generation. It should be a long and secure string.

Now you can restart the server and try to log in.

> Login: `admin@amsdal.com` <br/>
> Password: `DemoPassword1234!` <br/>
> API Url: `http://localhost:8080`

Now, let’s fill our database with some data.

## Step 5 - Fixtures

We will use fixtures in order to fill our database. Let’s create fixtures for our Country model:


In [ ]:
from pathlib import Path

fixture_file = Path('./src/fixtures/country.json')
fixture_file.parent.mkdir(parents=True, exist_ok=True)
fixture_file.write_text('''{
    "Country": [
      {
        "external_id": "us",
        "name": "United States",
        "code": "US"
      },
      {
        "external_id": "gb",
        "name": "United Kingdom",
        "code": "GB"
      },
      {
        "external_id": "de",
        "name": "Germany",
        "code": "DE"
      }
    ]
}
''')

As you can see the `name` and the `code` are properties of our Country model. Although, we also have the `external_id`
which is just a unique key that you can use in the fixtures as a reference ID to these records. It can be any unique
string.

Now, let’s restart our local server, stop and start again - `amsdal serve`. Check results:

<div class="tabbed-set tabbed-alternate" data-tabs="1:2" style="--md-indicator-x: 0px; --md-indicator-width: 166px;"><input checked="checked" id="__tabbed_1_1" name="__tabbed_1" type="radio"><input id="__tabbed_1_2" name="__tabbed_1" type="radio"><div class="tabbed-labels tabbed-labels--linked"><label for="__tabbed_1_1"><a href="#__tabbed_1_1" tabindex="-1">AMSDAL Console</a></label><label for="__tabbed_1_2"><a href="#__tabbed_1_2" tabindex="-1">Swagger API</a></label></div>
<div class="tabbed-content">
<div class="tabbed-block">
<p>Go to <a href="https://console.amsdal.com/Country">https://console.amsdal.com/Country</a> and you will see there are our three countries:
</p><figure markdown="">
<img alt="Fixtures" src="/media/images/fixtures_1.png" width="750">
</figure><p></p>
</div>
<div class="tabbed-block">
<p>Go to <a href="http://localhost:8000/docs#/Objects/object_list_api_objects__get">http://localhost:8080/docs</a> and
scroll down to <code>Object List</code> API. Click on <code>Try it out</code> and put <code>Country</code> into <code>class_name</code> field, hit an <code>Execute</code>.
You will get JSON response with your countries that were created from fixtures.</p>
</div>
</div>
<div class="tabbed-control tabbed-control--prev" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div><div class="tabbed-control tabbed-control--next" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div></div>

Let’s do the same for the Property model:

In [ ]:
fixture_file = Path('./src/fixtures/properties.json')
fixture_file.write_text('''{
    "Property": [
      {
        "external_id": "7fe17f0a-2c63-4076-b0fb-0a75022c489f",
        "name": "Freehand Los Angeles",
        "type": "Hotel",
        "address": "416 W 8th St",
        "free_parking": true,
        "free_wifi": true,
        "photos": [
          "Property/1.png",
          "Property/2.png",
          "Property/3.png"
        ]
      },
      {
        "external_id": "098e6218-75bf-4728-a844-196884ed6a90",
        "name": "Murray Hill East Suites",
        "type": "Apartment",
        "address": "149 E 39th St",
        "free_parking": false,
        "free_wifi": true,
        "photos": [
          "Property/4.png",
          "Property/5.png"
        ]
      },
      {
        "external_id": "355d1b05-182c-48ca-b792-aba237dafa9b",
        "name": "Hafenhaus Gager",
        "type": "Country House",
        "address": "Hauptstraße 1",
        "free_parking": true,
        "free_wifi": false,
        "photos": [
          "Property/6.png",
          "Property/7.png"
        ]
      }
    ]
}''')

As you can see, these fixtures include the photos. For example, the `"Property/6.jpeg"` means that it should use the
photo located in the `./src/fixtures/files/Property/` directory. So we need to put photos there:

In [ ]:
from pathlib import Path
import shutil

source_dir = Path(notebook_dir) / "photos"
destination_dir = Path('./src/fixtures/files/Property')

# Create destination directory if it doesn't exist
destination_dir.mkdir(parents=True, exist_ok=True)

# Copy files from source to destination
for file_path in source_dir.iterdir():
    if file_path.is_file():
        shutil.copy(file_path, destination_dir)

Now, let’s re-run our local API server and see the results by the following link:

[https://console.amsdal.com/Property](https://console.amsdal.com/Property)

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about the fixtures, see the following
documentation: <a href="/models/fixtures/">Fixtures</a></p>
</div>

<div class="admonition tip">
<p class="admonition-title">Tip</p>
<p>If you check how the response is returned via API
<a href="http://localhost:8080/docs#/Objects/object_list_api_objects__get">Objects list</a> for Property class name, you will
notice that binary data of images are returned in base64 format prefixed with <code>data:binary;base64,</code>. It's because
JSON does not support binary data. It means, if you want to create objects with binary properties via API you need
to encode the binary value to base64 and send it in the same format: <code>data:binary;base64, YOUR-BASE64-DATA</code>.</p>
</div>

Now, let’s add some business logic, for example, we don’t want to allow to create of a journey with a non-adult person ( a person aged less than 18).

## Step 6 - Adding hooks

Hooks allow you to add custom logic to the model's lifecycle.
For example, you can add a hook that will be executed before the model is saved to the database.

We will use the `apre_create` hook on the Journey model in order to achieve this. Although, when we use Python models, CLI command `amsdal generate hook` will not create the hooks. You need to create the hooks manually inside the python class of your model. Let's create an async `apre_create` hook for the Journey model. First of all let's check the content of the Journey model:

In [ ]:
from pathlib import Path

model_file = Path('./src/models/journey.py')
content = model_file.read_text()

print('Journey model content:')
print(content)

We need to define our hook inside `Journey` class, so our class should be the next:

```python
class Journey(Model):
    __module_type__: ClassVar[ModuleType] = ModuleType.USER
    start_date: Optional[str] = Field(None, title='start_date')
    end_date: Optional[str] = Field(None, title='end_date')
    country: Optional['Country'] = Field(None, title='country')
    persons: Optional[list['Person']] = Field(None, title='persons')
    equipment: Optional[dict[str, Optional[float]]] = Field(None, title='equipment')
    bookings: Optional[list['Booking']] = Field(None, title='bookings')

    @field_validator('equipment')
    @classmethod
    def _non_empty_keys_equipment(cls: type, value: Any) -> Any:
        return validate_non_empty_keys(value)
    
    async def apre_create(self) -> None:
        await self.validate_persons_age()

    async def validate_persons_age(self) -> None:
        from models.person import Person

        for index, person_reference in enumerate(self.persons or []):
            person: Person

            if isinstance(person_reference, Person):
                person = person_reference
            elif isinstance(person_reference, Reference):
                person = await person_reference
            else:
                person = await Reference(**person_reference)

            try:
                birthdate = datetime.strptime(person.dob, "%Y-%m-%d")
            except (TypeError, ValueError):
                continue

            today = date.today()
            age = today.year - birthdate.year - ((today.month, today.day) < (birthdate.month, birthdate.day))

            if age < 18:
                raise ValueError(f"{person.first_name} {person.last_name}: Age must be 18 or older")

```

As you can notice, we also use `date`, `datetime` and `Reference` that we need to import:
```python
from datetime import datetime
from datetime import date

from amsdal import Reference
```

Let's put it all to our model:

In [ ]:
content = '''
from datetime import datetime
from datetime import date
from typing import Any
from typing import ClassVar
from typing import Optional

from amsdal import Reference
from amsdal_models.builder.validators.dict_validators import validate_non_empty_keys
from amsdal_models.classes.model import Model
from amsdal_utils.models.enums import ModuleType
from pydantic.fields import Field
from pydantic.functional_validators import field_validator

from models.booking import *
from models.country import *
from models.person import *


class Journey(Model):
    __module_type__: ClassVar[ModuleType] = ModuleType.USER
    start_date: Optional[str] = Field(None, title='start_date')
    end_date: Optional[str] = Field(None, title='end_date')
    country: Optional['Country'] = Field(None, title='country')
    persons: Optional[list['Person']] = Field(None, title='persons')
    equipment: Optional[dict[str, Optional[float]]] = Field(None, title='equipment')
    bookings: Optional[list['Booking']] = Field(None, title='bookings')

    @field_validator('equipment')
    @classmethod
    def _non_empty_keys_equipment(cls: type, value: Any) -> Any:
        return validate_non_empty_keys(value)
    
    async def apre_create(self) -> None:
        await self.validate_persons_age()

    async def validate_persons_age(self) -> None:
        from models.person import Person

        for index, person_reference in enumerate(self.persons or []):
            person: Person

            if isinstance(person_reference, Person):
                person = person_reference
            elif isinstance(person_reference, Reference):
                person = await person_reference
            else:
                person = await Reference(**person_reference)

            try:
                birthdate = datetime.strptime(person.dob, "%Y-%m-%d")
            except (TypeError, ValueError):
                continue

            today = date.today()
            age = today.year - birthdate.year - ((today.month, today.day) < (birthdate.month, birthdate.day))

            if age < 18:
                raise ValueError(f"{person.first_name} {person.last_name}: Age must be 18 or older")
'''

# Write the updated content to the file
model_file.write_text(content)

print()
print('Updated Journey model content:')
print(model_file.read_text())

Note, we will check the age if only this is a creation, not updating. Also, we assume the DOB is stored in `YYYY-MM-DD`
format.

The important thing here is that all related objects can be passed either as an instance of an object or a reference. In
our case, the list of people is the list of references. Therefore, in order to get the actual object by reference
we need to construct the Reference object and await it.
We can handle all the cases by the following code:

```python
if isinstance(person_reference, Person):
    person = person_reference
elif isinstance(person_reference, Reference):
    person = await person_reference
else:
    person = await Reference(**person_reference)
```

Now, the person is an instance of the Person model with corresponding properties and values.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about references, see the following
documentation: <a href="/models/schemas/#referencesrelationships">References</a></p>
</div>

Also, note how we raise the validation errors, you can raise built-in `ValueError` exception.

Since we have made changes to the models we need to create and apply new migrations. Run the following commands:


In [ ]:
!amsdal migrations new
!amsdal migrations apply

Let’s restart our API server `amsdal serve` and create a Person with an age less than 18 and try to add this person to a
journey.

<div class="tabbed-set tabbed-alternate" data-tabs="4:2" style="--md-indicator-x: 0px; --md-indicator-width: 166px;"><input checked="checked" id="__tabbed_4_1" name="__tabbed_4" type="radio"><input id="__tabbed_4_2" name="__tabbed_4" type="radio"><div class="tabbed-labels tabbed-labels--linked"><label for="__tabbed_4_1"><a href="#__tabbed_4_1" tabindex="-1">AMSDAL Console</a></label><label for="__tabbed_4_2"><a href="#__tabbed_4_2" tabindex="-1">Swagger API</a></label></div>
<div class="tabbed-content">
<div class="tabbed-block">
<ol>
<li>Go to <a href="https://console.amsdal.com/Person">https://console.amsdal.com/Person</a> and click on <code>Create</code> button.</li>
<li>Fill the form in, the first name, the last name, and put DOB so our person will have an age less than 18, in format <code>YYYY-MM-DD</code></li>
<li>And click on the <code>Submit</code>
So, you should see something like:
<img alt="" src="/media/images/persons_list.png"></li>
</ol>
</div>
<div class="tabbed-block">
<ol>
<li>Go to <a href="http://localhost:8000/docs#/Objects/object_create_api_objects__post">http://localhost:8000/docs</a> and scroll
down to <code>Object Create</code> API, click on <code>Try it out</code>.</li>
<li>Fill the <code>class_name</code> field with <code>Person</code></li>
<li>Put the following JSON into request body:
<div class="language-json highlight"><pre id="__code_13"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_13 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"first_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Kara"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"last_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Lloyd"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"dob"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2020-05-12"</span>
<span class="p">}</span>
</code></pre></div>
You should get <code>201</code> status code and the created person in response body, something like:
<div class="language-json highlight"><pre id="__code_14"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_14 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"first_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Kara"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"last_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Lloyd"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"dob"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2020-05-12"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"_metadata"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">    </span><span class="nt">"address"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"resource"</span><span class="p">:</span><span class="w"> </span><span class="s2">"sqlite_state"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"class_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Person"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"class_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"a7087c0f82c0465f8223977c37ef4272"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"object_id"</span><span class="p">:</span><span class="w"> </span><span class="s2">"3c1eb6f90c8d4a4a870d47c3dafdb207"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"object_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"42bbc479be054f4e874bbfcc78771e52"</span>
<span class="w">    </span><span class="p">},</span>
<span class="w">    </span><span class="nt">"class_schema_reference"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">        </span><span class="nt">"resource"</span><span class="p">:</span><span class="w"> </span><span class="s2">"sqlite_state"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"class_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"ClassObject"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"class_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"fd6b5582025146209b675e35455dd32f"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"object_id"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Person"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"object_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"a7087c0f82c0465f8223977c37ef4272"</span>
<span class="w">      </span><span class="p">}</span>
<span class="w">    </span><span class="p">},</span>
<span class="w">    </span><span class="err">...</span>
<span class="w">  </span><span class="p">},</span>
<span class="w">  </span><span class="err">...</span>
<span class="p">}</span>
</code></pre></div>
The important here is the value under <code>_metadata.address</code> key. It's the address of the object that we can use as a
reference. We will use it just in a moment.</li>
</ol>
</div>
</div>
<div class="tabbed-control tabbed-control--prev" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div><div class="tabbed-control tabbed-control--next" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div></div>

Now let’s try to add this person to a new journey:

<div class="tabbed-set tabbed-alternate" data-tabs="5:2" style="--md-indicator-x: 0px; --md-indicator-width: 166px;"><input checked="checked" id="__tabbed_5_1" name="__tabbed_5" type="radio"><input id="__tabbed_5_2" name="__tabbed_5" type="radio"><div class="tabbed-labels tabbed-labels--linked"><label for="__tabbed_5_1"><a href="#__tabbed_5_1" tabindex="-1">AMSDAL Console</a></label><label for="__tabbed_5_2"><a href="#__tabbed_5_2" tabindex="-1">Swagger API</a></label></div>
<div class="tabbed-content">
<div class="tabbed-block">
<ol>
<li>Go to <a href="https://console.amsdal.com/Journey">https://console.amsdal.com/Journey</a> and click on the <code>Create</code> button</li>
<li>Fill in the start date and the end date in the format <code>YYYY-MM-DD</code>, e.g. 2023-08-01 and 2023-08-10, select any country and add our person.
You should see something like:
<img alt="" src="/media/images/create_journey_form.png">
Now, click on <code>Submit</code>, you will see the error message:
<img alt="" src="/media/images/create_journey_validation_error.png"></li>
</ol>
</div>
<div class="tabbed-block">
<ol>
<li>Got to <a href="http://localhost:8000/docs#/Objects/object_create_api_objects__post">http://localhost:8000/docs</a> and scroll
down to <code>Object Create</code> API, click on <code>Try it out</code>.</li>
<li>Fill the <code>class_name</code> field with <code>Journey</code></li>
<li>Put the following JSON as a request body:
<div class="language-json highlight"><pre id="__code_15"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_15 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"start_date"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2030-08-01"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"end_date"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2030-08-10"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"country"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="err">COUNTRY_ADDRESS</span><span class="p">},</span>
<span class="w">  </span><span class="nt">"persons"</span><span class="p">:</span><span class="w"> </span><span class="p">[{</span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="err">PERSON_ADDRESS</span><span class="p">}]</span>
<span class="p">}</span>
</code></pre></div></li>
<li>Before submitting, we need to replace <code>COUNTRY_ADDRESS</code> and <code>PERSON_ADDRESS</code> with actual addresses. The
<code>PERSON_ADDRESS</code> you can get from previous request. The <code>COUNTRY_ADDRESS</code> one - from the response of Object List
API, just pick <code>_metadata.address</code> of any country and put it here as it is.
So you should have something like this:
<div class="language-json highlight"><pre id="__code_16"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_16 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"start_date"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2030-08-01"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"end_date"</span><span class="p">:</span><span class="w"> </span><span class="s2">"2030-08-10"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"country"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">    </span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"resource"</span><span class="p">:</span><span class="w"> </span><span class="s2">"sqlite_state"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"class_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Country"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"class_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"51c77e43822441709a4d4b45f2f7c51b"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"object_id"</span><span class="p">:</span><span class="w"> </span><span class="s2">"us"</span><span class="p">,</span>
<span class="w">      </span><span class="nt">"object_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"a6044862269a48ce9a05627b850ec472"</span>
<span class="w">    </span><span class="p">}</span>
<span class="w">  </span><span class="p">},</span>
<span class="w">  </span><span class="nt">"persons"</span><span class="p">:</span><span class="w"> </span><span class="p">[</span>
<span class="w">    </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">        </span><span class="nt">"resource"</span><span class="p">:</span><span class="w"> </span><span class="s2">"sqlite_state"</span><span class="p">,</span><span class="w"> </span>
<span class="w">        </span><span class="nt">"class_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Person"</span><span class="p">,</span><span class="w"> </span>
<span class="w">        </span><span class="nt">"class_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"af7ef113a01a4240856154ef2dacf4db"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"object_id"</span><span class="p">:</span><span class="w"> </span><span class="s2">"230b2021fa0646a0892b5ee27afe8996"</span><span class="p">,</span>
<span class="w">        </span><span class="nt">"object_version"</span><span class="p">:</span><span class="w"> </span><span class="s2">"31918790b0474aefa26074d1ff7efd8b"</span><span class="w">    </span>
<span class="w">      </span><span class="p">}</span>
<span class="w">    </span><span class="p">}</span>
<span class="w">  </span><span class="p">]</span>
<span class="p">}</span>
</code></pre></div></li>
<li>Click on <code>Execute</code> and you will get <code>400</code> status code and the following JSON response:
<div class="language-json highlight"><pre id="__code_17"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_17 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"detail"</span><span class="p">:</span><span class="w"> </span><span class="s2">"Kara Lloyd: Age must be 18 or older"</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"control"</span><span class="p">:</span><span class="w"> </span><span class="err">...</span>
<span class="p">}</span>
</code></pre></div></li>
</ol>
</div>
</div>
<div class="tabbed-control tabbed-control--prev" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div><div class="tabbed-control tabbed-control--next" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div></div>

Perfect!

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about all available hooks, see the following
documentation: <a href="/models/hooks/">Generate Hooks</a></p>
</div>

You might notice how the records are displayed in select fields on the AMSDAL Console:

![](/media/images/select_box_values_unformatted.png)

It’s not quite informative, so let’s improve it.

## Step 7 - Creating a display name modifier

The modifier, it’s a predefined method that allows you to override some specific built-in methods or properties of your
end models. The AMSDAL CLI command `amsdal generate modifier` will not work for Python models, so we need to create them manually.

Let’s open `./src/models/country.py` file and add `display_name` dynamic property to the `Country` model:

In [ ]:
country_model = Path('./src/models/country.py')
display_name = '''
    @property
    def display_name(self) -> str:
        return self.name
'''

content = country_model.read_text()
country_model.write_text(content + display_name)

print('Updated Country model content:')
print(country_model.read_text())

The `self` is our instance of the Country model, so we can access any of the fields of this model. In our case, it’s
enough to just return the country name and show it in UI.

Now, let’s change `src/models/person.py` and add the next `display_name`:

In [ ]:
person_model = Path('./src/models/person.py')
display_name = '''
    @property
    def display_name(self) -> str:
        from datetime import datetime
        from datetime import date

        today = date.today()

        try:
            birthdate = datetime.strptime(self.dob, "%Y-%m-%d")
        except (TypeError, ValueError):
            age = "N/A"
        else:
            age = today.year - birthdate.year - ((today.month, today.day) < (birthdate.month, birthdate.day))

        return f"{self.first_name} {self.last_name} ({age} years old)"
'''

content = person_model.read_text()
person_model.write_text(content + display_name)

print('Updated Person model content:')
print(person_model.read_text())

As you can see we access two fields of the Person model and combine them to the string using Python’s `f` string
functionality to have the full name of a person.

Let's not forget to make the migrations:

In [ ]:
!amsdal migrations new
!amsdal migrations apply

Now, if you will restart the server:

<div class="tabbed-set tabbed-alternate" data-tabs="6:2" style="--md-indicator-x: 0px; --md-indicator-width: 166px;"><input checked="checked" id="__tabbed_6_1" name="__tabbed_6" type="radio"><input id="__tabbed_6_2" name="__tabbed_6" type="radio"><div class="tabbed-labels tabbed-labels--linked"><label for="__tabbed_6_1"><a href="#__tabbed_6_1" tabindex="-1">AMSDAL Console</a></label><label for="__tabbed_6_2"><a href="#__tabbed_6_2" tabindex="-1">Swagger API</a></label></div>
<div class="tabbed-content">
<div class="tabbed-block">
<p>And during creation a journey you will see something like this:
<img alt="" src="/media/images/display_name_modifier.png"></p>
</div>
<div class="tabbed-block">
<p>And using the <code>Object List</code> API for these models, in JSON response you will get an extra <code>display_name</code> field:
</p><div class="language-json highlight"><pre id="__code_22"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_22 > code"></button><code><span class="w">  </span><span class="err">...</span>
<span class="w">  </span><span class="p">{</span>
<span class="w">    </span><span class="nt">"name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"United States"</span><span class="p">,</span>
<span class="w">    </span><span class="nt">"code"</span><span class="p">:</span><span class="w"> </span><span class="s2">"US"</span><span class="p">,</span>
<span class="w">    </span><span class="nt">"display_name"</span><span class="p">:</span><span class="w"> </span><span class="s2">"United States"</span><span class="p">,</span>
<span class="w">    </span><span class="err">...</span><span class="p">,</span>
<span class="w">  </span><span class="p">},</span>
<span class="w">  </span><span class="err">...</span>
</code></pre></div><p></p>
</div>
</div>
<div class="tabbed-control tabbed-control--prev" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div><div class="tabbed-control tabbed-control--next" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div></div>

Perfect!

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about all available modifiers, see the following
documentation: <a href="/models/modifiers/">Generate Modifiers</a></p>
</div>

You might notice that we already had similar functionality for calculating the age. We did this in the `pre_init` hook.
Let’s keep following the DRY (Don't repeat yourself) principle and move this functionality to the custom property of the
Person model.

## Step 8 - Creating a custom property

Again, for Python models, the `amsdal generate property` command will not work, so we need to create it manually. Let's create custom property `age` for our Person model:

In [ ]:
age_property = '''
    @property
    def age(self):
        from datetime import datetime
        from datetime import date

        today = date.today()

        try:
            birthdate = datetime.strptime(self.dob, "%Y-%m-%d")
        except (TypeError, ValueError):
            return "N/A"
        else:
            return today.year - birthdate.year - ((today.month, today.day) < (birthdate.month, birthdate.day))
'''

content = person_model.read_text()
person_model.write_text(content + age_property)

print('Updated Person model content:')
print(person_model.read_text())

Now, we can use this property in the `pre_create` hook for Journey model. Let's adjust the `src/models/journey.py`
to the following:

In [ ]:
model_file = Path('./src/models/journey.py')
content = '''
from typing import Any
from typing import ClassVar
from typing import Optional

from amsdal import Reference
from amsdal_models.builder.validators.dict_validators import validate_non_empty_keys
from amsdal_models.classes.model import Model
from amsdal_utils.models.enums import ModuleType
from pydantic.fields import Field
from pydantic.functional_validators import field_validator

from models.booking import *
from models.country import *
from models.person import *


class Journey(Model):
    __module_type__: ClassVar[ModuleType] = ModuleType.USER
    start_date: Optional[str] = Field(None, title='start_date')
    end_date: Optional[str] = Field(None, title='end_date')
    country: Optional['Country'] = Field(None, title='country')
    persons: Optional[list['Person']] = Field(None, title='persons')
    equipment: Optional[dict[str, Optional[float]]] = Field(None, title='equipment')
    bookings: Optional[list['Booking']] = Field(None, title='bookings')

    @field_validator('equipment')
    @classmethod
    def _non_empty_keys_equipment(cls: type, value: Any) -> Any:
        return validate_non_empty_keys(value)

    async def apre_create(self) -> None:
        await self.validate_persons_age()

    async def validate_persons_age(self) -> None:
        from models.person import Person

        for index, person_reference in enumerate(self.persons or []):
            person: Person

            if isinstance(person_reference, Person):
                person = person_reference
            elif isinstance(person_reference, Reference):
                person = await person_reference
            else:
                person = await Reference(**person_reference)

            if person.age == "N/A":
                raise ValueError("Invalid DOB format. Please use YYYY-MM-DD")

            if person.age < 18:
                raise ValueError(
                    f"{person.first_name} {person.last_name}: Age must be 18 or older"
                )
'''

# Write the updated content to the file
model_file.write_text(content)

print()
print('Updated Journey model content:')
print(model_file.read_text())

It’s much clear now, is it?

Let’s do the same for the `display_name` modifier of the Person model, to use the `age` property instead of the duplicated code:

```
@property
def display_name(self) -> str:
    return f"{self.first_name} {self.last_name} ({self.age} years old)"
```

In [ ]:
person_model.write_text('''
from typing import ClassVar
from typing import Optional

from amsdal_models.classes.model import Model
from amsdal_utils.models.enums import ModuleType
from pydantic.fields import Field


class Person(Model):
    __module_type__: ClassVar[ModuleType] = ModuleType.USER
    first_name: Optional[str] = Field(None, title='first_name')
    last_name: Optional[str] = Field(None, title='last_name')
    dob: Optional[str] = Field(None, title='dob')

    @property
    def display_name(self) -> str:
        return f"{self.first_name} {self.last_name} ({self.age} years old)"

    @property
    def age(self):
        from datetime import datetime
        from datetime import date

        today = date.today()

        try:
            birthdate = datetime.strptime(self.dob, "%Y-%m-%d")
        except (TypeError, ValueError):
            return "N/A"
        else:
            return today.year - birthdate.year - ((today.month, today.day) < (birthdate.month, birthdate.day))
''')

Don't forget to **create migrations**:

In [ ]:
!amsdal migrations new
!amsdal migrations apply

And now try to restart the server and check it out.

Perfect! Our custom properties will now be displayed as a separate column, for example for [Person](https://console.amsdal.com/Person) we now have an “Age” column. Now it is much more readable!

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about the custom properties, see the following
documentation: <a href="/cli/overview/#generate-custom-properties">Generate Custom Properties</a></p>
</div>

Now, let’s create a transaction that will plan our journey.

## Step 9 - Creating a transaction

### General

We will use the **Transaction** feature. The transaction is a kind of function that can combine complex business logic.
It can accept the parameters and return some results. In this document, we will create two transactions:

- **BuildJourney** - this transaction will generate a journey and book hotels. We will learn how to build complex logic
  and how to use the **Model** creation in practice.
- **GenerateReport** - this transaction will generate a report based on the upcoming journey. We will learn how to use
  the
  **QuerySets**, how to add to the application external python libraries.

### The journey builder transaction

This transaction will generate a journey and book hotels. In the real world, it would generate it based on the trends or
other criteria, although for simplification we will generate it just randomly.

So, this transaction will accept the following params:

- **countries** - list of possible countries we want to visit.
- **nights** - how many nights at each stay
- **total_nights** - how long the whole journey will take e
- **persons** - list of persons who will attend this journey
- **equipment** - key-value for storing some equipment and quantity for this journey

Let’s generate a transaction blueprint by running the following command:

In [ ]:
!amsdal generate transaction BuildJourney

It will create the `src/transactions/build_journey.py` file, let's change it to the following:


In [ ]:
transaction = Path('./src/transactions/build_journey.py')
transaction.write_text('''
import random
from datetime import date, timedelta
from datetime import datetime

from amsdal.transactions import async_transaction
from models.booking import Booking
from models.country import Country
from models.journey import Journey
from models.person import Person
from models.property import Property


@async_transaction
async def BuildJourney(
    countries: list[Country],
    nights: int,
    total_nights: int,
    persons: list[Person],
    equipment: dict[str, int],
):
    country = get_country_by_trend(countries)
    start_date = get_best_start_date(country)
    bookings = await book_best_properties(country, start_date, nights, total_nights)
    last_booking = bookings[-1]
    end_date = datetime.strptime(last_booking.date, "%Y-%m-%d") + timedelta(
        days=last_booking.nights
    )
    journey_start_date = start_date.strftime("%Y-%m-%d")
    journey_end_date = end_date.strftime("%Y-%m-%d")

    journey = Journey(
        start_date=journey_start_date,
        end_date=journey_end_date,
        country=country,
        persons=persons,
        equipment=equipment,
        bookings=bookings,
    )
    await journey.asave()

    return {
        "start_date": journey.start_date,
    }


def get_country_by_trend(countries: list[Country]) -> Country:
    if len(countries) == 0:
        raise ValueError("No countries specified")

    # TODO: get the most trending country for the current year
    return random.choice(countries)


def get_best_start_date(country: Country) -> date:
    # TODO: here we can check a weather forecast for the country and find the best closest start date
    return date.today() + timedelta(days=random.randint(30, 45))


async def book_best_properties(
    country: Country,
    start_date: date,
    nights: int,
    total_nights: int,
):
    # TODO: here we can use external API to find the best properties for the country and book the available ones
    bookings = []
    properties = await Property.objects.all().aexecute()
    rest_nights = total_nights

    if len(properties) == 0:
        raise ValueError(
            f"No properties found for the country: {country.name}"
        )

    while len(properties) > 0 and rest_nights > 0:
        _property = random.choice(properties)
        properties.remove(_property)

        if not len(properties) or rest_nights <= 2 * nights:
            book_nights = rest_nights
            rest_nights = 0
        else:
            book_nights = nights
            rest_nights -= nights

        booking = await Booking(
            property=_property,
            date=start_date.strftime("%Y-%m-%d"),
            nights=book_nights,
        ).asave()
        bookings.append(booking)

    return bookings
''')

Let’s see what we do there. First of all, the `async def BuildJourney(...)` is our transaction, and as you can see it
accepts all arguments that we described before.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>⚠️ The important thing here is to annotate all arguments of transactions with types. It helps to properly understand and
accept them when you use API to execute these transactions (see <strong>POST</strong> to <code>/transactions/{transactionname}</code> in the
Swagger documentation).</p>
</div>

All other functions (e.g. `get_country_by_trend`, `get_best_start_date`, etc.) are just helpers that we use inside our
transaction. You can put the whole logic just inside the `BuildJourney` function, although splitting it into smaller
functions provides a better understanding of the code.

The idea of this transaction is:

1. it gets one of the passed countries, the most popular country for this year. Although for simplification we just take
   the country randomly.
2. After that, we resolve the best start date of the journey. For example, we can check the weather forecast for
   resolved country and pick the warmest day. Although for simplification, we just take it randomly as well.
3. Then we search the most popular properties for this country and for journey dates and book them. Again, we can use
   some 3rd-party integration to find the best properties, although for simplification we just take them all from our
   pre-defined database. Note, we loop through our properties and book one by one until we will book a number of nights
   equal to provided `total_nights` argument.
4. And when we have a list of bookings, we create our Journey object and put there all referenced objects.

This transaction demonstrates how can we build the complex business logic and create records and store them in DB. As
you can see, in order to create and store an object you need just create an instance of this object.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about object creation and updating see the following
documentation: <a href="/models/schemas/">Model instances</a></p>
</div>

Let’s now build one more transaction that will build a report.

### Report generation transaction

Let’s build the transaction that will generate a report about the upcoming journey in HTML format, and also will include
the history of any changes related to it.

Assume we want to generate the following layout for our HTML report:

![](/media/images/report_template.png)

The business logic will be the following:

1. Our transaction function will not accept arguments
2. It will take the first upcoming journey and collect the stored information from DB
3. Then we will put this information into an HTML template and render the HTML page
4. After that, we will just write this HTML to a file system, although it can be sent via E-mail in the real-world
   project.

First of all, we need to extend our Journey model and add the `start_timestamp` field with the `number` type to have the
ability to filter and order our journeys easily. Open `src/models/journey.py` and add this property just next to
the `start_date`:

In [ ]:
print(working_directory)
journey_model = Path('./src/models/journey.py')
journey_model.write_text('''
from typing import Any
from typing import ClassVar
from typing import Optional

from amsdal import Reference
from amsdal_models.builder.validators.dict_validators import validate_non_empty_keys
from amsdal_models.classes.model import Model
from amsdal_utils.models.enums import ModuleType
from pydantic.fields import Field
from pydantic.functional_validators import field_validator

from models.booking import *
from models.country import *
from models.person import *


class Journey(Model):
    __module_type__: ClassVar[ModuleType] = ModuleType.USER
    start_date: Optional[str] = Field(None, title='start_date')
    start_timestamp: Optional[float] = Field(None, title='start_timestamp')
    end_date: Optional[str] = Field(None, title='end_date')
    country: Optional['Country'] = Field(None, title='country')
    persons: Optional[list['Person']] = Field(None, title='persons')
    equipment: Optional[dict[str, Optional[float]]] = Field(None, title='equipment')
    bookings: Optional[list['Booking']] = Field(None, title='bookings')

    @field_validator('equipment')
    @classmethod
    def _non_empty_keys_equipment(cls: type, value: Any) -> Any:
        return validate_non_empty_keys(value)

    async def apre_create(self) -> None:
        await self.validate_persons_age()

    async def validate_persons_age(self) -> None:
        from models.person import Person

        for index, person_reference in enumerate(self.persons or []):
            person: Person

            if isinstance(person_reference, Person):
                person = person_reference
            elif isinstance(person_reference, Reference):
                person = await person_reference
            else:
                person = await Reference(**person_reference)

            if person.age == "N/A":
                raise ValueError("Invalid DOB format. Please use YYYY-MM-DD")

            if person.age < 18:
                raise ValueError(
                    f"{person.first_name} {person.last_name}: Age must be 18 or older"
                )
''')

print('Updated Journey model content:')
print(journey_model.read_text())

Now, let’s add functionality that will set this timestamp automatically based on the `start_date` value. We will do that
in `post_init` hook, so we need to adjust the `Journey` model and then put the functionality there:

In [ ]:
post_init_hook = '''
    def post_init(self, is_new_object, kwargs):
        from datetime import datetime

        try:
            start_date = datetime.strptime(self.start_date, "%Y-%m-%d")
        except (TypeError, ValueError):
            self.start_timestamp = None
        else:
            self.start_timestamp = start_date.timestamp()
    '''

content = journey_model.read_text()
journey_model.write_text(content + post_init_hook)

print('Updated Journey model content:')
print(journey_model.read_text())

This hook will be executed after the instance is initialized and validation was proceed, so we can access instance
properties via `self`.

After these changes, you need to make migrations:

In [ ]:
!amsdal migrations new
!amsdal migrations apply

Now, let’s run the following command to generate a new transaction blueprint:

In [ ]:
!amsdal generate transaction GenerateReport

And change the generated file to the following:

In [ ]:
generate_report = Path('./src/transactions/generate_report.py')
generate_report.write_text('''
import base64

import jinja2
from datetime import datetime

from amsdal import Metadata
from amsdal import Versions
from amsdal import Reference
from amsdal.models import Model
from amsdal.transactions import async_transaction

from models.booking import Booking
from models.journey import Journey
from models.person import Person


@async_transaction
async def GenerateReport():
    upcoming_journey = await get_upcoming_journey()

    if not upcoming_journey:
        raise ValueError("No upcoming journey found")

    # Preload the m2m relationships
    await upcoming_journey.persons
    await upcoming_journey.bookings

    history_changes = await get_history_changes(upcoming_journey)
    html_buffer = await render_html(upcoming_journey, history_changes)

    # Send this HTML in E-mail, although we will just write to the file
    with open("report.html", "wt") as f:
        f.write(html_buffer)

    return {
        "html": html_buffer,
    }
''')

This is not yet ready for running because we need to implement each of these internal functions, although it gives us an
understanding of the transaction business logic:

1. So first of all, we need to get the upcoming journey from DB `upcoming_journey = await get_upcoming_journey()`
2. Then we check that we have a journey, otherwise, we raise the validation error
3. After that, we get the history changes for this journey `history_changes = await get_history_changes(upcoming_journey)`
4. Then we render the HTML page `html_buffer = render_html(upcoming_journey, history_changes)`
5. And finally, we write this HTML to the file system

Let’s start implementing the first inner function - `get_upcoming_journey()`:

In [ ]:
content = generate_report.read_text()
generate_report.write_text(content + '''
async def get_upcoming_journey():
    qs = Journey.objects.filter(start_timestamp__gt=datetime.now().timestamp())
    qs = qs.order_by("start_timestamp")

    return await qs.first().aexecute()
''')

We just put this function next to our `GenerateReport()` function as we did it in the previous transaction. As you can see,
we build a **QuerySet** and first of all filter _Journeys_ that have `start_timestamp` greater than the current
timestamp.

After that, we add ordering to this **QuerySet** by `qs.order_by("start_timestamp")` which means we need to order our
records by the `start_timestamp` field in the ASC direction.

Each applied function to the **QuerySet**, e.g. `filter`, `order_by`, `first`, etc., will return a new **QuerySet**
object. So the **QuerySet** is a kind of immutable object, therefore we override the `qs` variable after applying the
ordering. The `first` will just take the first record from the ordered list.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>📎 If you want to know more about <strong>QuerySets</strong>, see the following documentation:
<a href="/models/queryset/queryset/">QuerySets</a></p>
</div>

OK, now let’s implement the next function - `get_history_changes(upcoming_journey)`. This function should return the
list of changes, for example, in the following format:

```python
[
    {"date": "2023-04-10", "model": "Person", "action": "changed", "display_name": "Julian Lange"},
    ...
]
```

So we later can render the list of changes in our PDF report. The implementation of this function can be the following:

In [ ]:
content = generate_report.read_text()
generate_report.write_text(content + '''
async def get_history_changes(journey: Journey):
    history = []

    # get all history changes for the journey itself
    history.extend(await _get_history_changes_for_model(Journey, journey, "Journey"))

    # get all history changes for the bookings
    for booking in journey.bookings:
        history.extend(await _get_history_changes_for_model(Booking, booking, "Booking"))

    # get all history changes for the persons
    for person in journey.persons:
        history.extend(await _get_history_changes_for_model(Person, person, "Person"))

    # sort history by order_key
    history.sort(key=lambda x: x["order_key"])

    return history


async def _get_history_changes_for_model(model, obj: Model | Reference, model_name):
    history = []

    qs = model.objects.filter(
        _address__class_version=Versions.ALL,
        _address__object_id=obj.object_id if isinstance(obj, Model) else obj.ref.object_id,
        _address__object_version_id=Versions.ALL,
    )

    item: Model
    for item in await qs.aexecute():
        history.append(
            {
                "order_key": (await item.aget_metadata()).updated_at,
                "date": _ms_to_date((await item.aget_metadata()).updated_at),
                "model": model_name,
                "action": _resolve_action((await item.aget_metadata())),
                "display_name": getattr(
                    item, "display_name", str((await item.aget_metadata()).address)
                ),
            }
        )

    return history


def _ms_to_date(ms: int):
    return datetime.fromtimestamp(ms / 1000).strftime("%Y-%m-%d")


def _resolve_action(metadata: Metadata):
    if metadata.is_deleted:
        return "Deleted"
    elif metadata.next_version:
        return "Changed"
    else:
        return "Created"
''')

As you can see we added a few more internal function-helpers just to get rid of code duplication.

Also, you can see we use the `_address__class_version=Versions.ALL` QuerySet filter in order to fetch all versions of
classes and the `_address__object_version_id=Versions.ALL` to fetch all versions of the object itself.

Now, let’s write the `render_html(upcoming_journey, history_changes)` function implementation. We will store the HTML
template separately as a static file. Therefore, let’s, first of all, create the directory `static` in the `src` one
and put there our `template.html`:

In [ ]:
template_path = Path(notebook_dir) / 'template.html'

print('Template:')
print(template_path.read_text())

destination_file = working_directory / 'src/static/template.html'
destination_file.parent.mkdir(parents=True, exist_ok=True)
destination_file.write_text(template_path.read_text())

In order to render this template we will use the **[Jinja2](https://jinja.palletsprojects.com/en/3.1.x/)** Python
library. So we need to add this package to our project and install it. Add the following line
(just below of `amsdal[cli]`) into the `requirements.txt` file located in the root of our project:


In [ ]:
requirements = Path('./requirements.txt')
requirements_text = requirements.read_text()
requirements.write_text(requirements_text + '\njinja2')

!pip install -r requirements.txt

Note, it’s important to have the exact `requirements.txt` file name for all our dependencies, so do not rename it.
Ok, now let’s implement our `render_html(upcoming_journey, history_changes)` function (just add it at the bottom of
the `src/transactions/generate_report.py` file):


In [ ]:
content = generate_report.read_text()
generate_report.write_text(content + '''
async def render_html(journey: Journey, history_changes: list):
    loader = jinja2.FileSystemLoader(searchpath="./static")
    env = jinja2.Environment(loader=loader, extensions=["jinja2.ext.loopcontrols"])

    def base64_encode(value):
        if not isinstance(value, bytes):
            raise TypeError("Input must be bytes")

        result = base64.b64encode(value).decode("utf-8")

        return f"data:image/jpeg;base64,{result}"

    env.filters["base64"] = base64_encode

    template = env.get_template("template.html")

    return template.render(
        journey=await journey.amodel_dump(),
        history_changes=history_changes,
    )
''')

As you can see, here we just initiate Jinja2 classes specifies `searchpath="./static"` where our template is located,
and render the template by passing there two variables - `journey` and `history_changes`. We also add a custom Jinja2
filter - `base64` just in order to display the image in HTML `<img src="..."/>` tag. As you can see, images are stored
in base64 as bytes, so we just decode them to string `value.decode("utf-8")` and build the
string `f"data:image/jpeg;base64,{result}"` that we put to the IMG tag.

Done! Let's check the whole `src/transactions/generate_report.py`:


In [ ]:
!cat ./src/transactions/generate_report.py

Let’s run our local server and check it - `amsdal serve`

<div class="tabbed-set tabbed-alternate" data-tabs="13:2" style="--md-indicator-x: 0px; --md-indicator-width: 166px;"><input checked="checked" id="__tabbed_13_1" name="__tabbed_13" type="radio"><input id="__tabbed_13_2" name="__tabbed_13" type="radio"><div class="tabbed-labels tabbed-labels--linked"><label for="__tabbed_13_1"><a href="#__tabbed_13_1" tabindex="-1">AMSDAL Console</a></label><label for="__tabbed_13_2"><a href="#__tabbed_13_2" tabindex="-1">Swagger API</a></label></div>
<div class="tabbed-content">
<div class="tabbed-block">
<ol>
<li>Go to the list of persons and create a Person with an age greater than 18.</li>
<li>Now go to transactions and execute the <code>BuildJourney</code> transaction.</li>
<li>After that go and run our <code>GenerateReport</code> transaction.</li>
</ol>
</div>
<div class="tabbed-block">
<ol>
<li>Use the <code>Object Create</code> API to create a Person with an age greater than 18 (see examples above).</li>
<li>Go to the <a href="http://localhost:8080/docs#/Transactions/transaction_execute_api_transactions__transaction_name___post">Transaction Execute API</a>
click on <code>Try it out</code>, put the <code>BuildJourney</code> into <code>transaction_name</code> field and the following JSON as request body:
<div class="language-json highlight"><pre id="__code_47"><span></span><button class="md-clipboard md-icon" title="Copy to clipboard" data-clipboard-target="#__code_47 > code"></button><code><span class="p">{</span>
<span class="w">  </span><span class="nt">"countries"</span><span class="p">:</span><span class="w"> </span><span class="p">[</span>
<span class="w">    </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="err">COUNTRY_ADDRESS</span>
<span class="w">    </span><span class="p">}</span>
<span class="w">  </span><span class="p">],</span>
<span class="w">  </span><span class="nt">"nights"</span><span class="p">:</span><span class="w"> </span><span class="mi">7</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"total_nights"</span><span class="p">:</span><span class="w"> </span><span class="mi">15</span><span class="p">,</span>
<span class="w">  </span><span class="nt">"persons"</span><span class="p">:</span><span class="w"> </span><span class="p">[</span>
<span class="w">    </span><span class="p">{</span>
<span class="w">      </span><span class="nt">"ref"</span><span class="p">:</span><span class="w"> </span><span class="err">PERSON_ADDRESS</span>
<span class="w">    </span><span class="p">}</span>
<span class="w">  </span><span class="p">],</span>
<span class="w">  </span><span class="nt">"equipment"</span><span class="p">:</span><span class="w"> </span><span class="p">{</span>
<span class="w">    </span><span class="nt">"ski"</span><span class="p">:</span><span class="w"> </span><span class="mi">1</span><span class="p">,</span>
<span class="w">    </span><span class="nt">"ski pass"</span><span class="p">:</span><span class="w"> </span><span class="mi">2</span>
<span class="w">  </span><span class="p">}</span>
<span class="p">}</span>
</code></pre></div>
Replace <code>COUNTRY_ADDRESS</code> and <code>PERSON_ADDRESS</code> with actual addresses and hit <code>Execute</code>. You should get a <code>200</code>
status code and <code>start_date</code> in JSON response.</li>
<li>Now, let's execute the second transaction, change the <code>transaction_name</code> to <code>GenerateReport</code>. This transaction
doesn't accept any arguments so put <code>{}</code> as a request body, hit the <code>Execute</code>. You will get a <code>200</code> status code and
HTML source of generated report.</li>
</ol>
</div>
</div>
<div class="tabbed-control tabbed-control--prev" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div><div class="tabbed-control tabbed-control--next" hidden=""><button class="tabbed-button" tabindex="-1" aria-hidden="true"></button></div></div>

Now, check the root directory of your project, you should see the `report.html` file. Try to open it in a browser
you should see something like this:
![](/media/images/report_result.png)

Now you know how to add 3rd party libraries to the AMSDAL application, add static files, and use the QuerySet to get
historical data.

## Step 10 - Deploy to cloud

Once you have completed the sign-up flow, you are able to deploy your application to AMSDAL Cloud.
In order to deploy it just run the following command from the root directory of your application and follow
the instructions:

In [ ]:
!amsdal cloud deploys new --no-input

Just after that you will get the URL of your future app, and the deploying process will be run.
The URL will be something like:
`https://main-1265b57653fd458ebdde6ffba78d3b8d.cloud.amsdal.com`

The swagger documentation will be accessible by `/docs` path,
e.g. `https://main-1265b57653fd458ebdde6ffba78d3b8d.cloud.amsdal.com/docs`

In order to check the status of the deploying use the following command:

In [ ]:
!amsdal cloud deploys --current-only

As soon as status will be changed from `deploying` to `deployed` you can use the URL of your app to access it.
Although, sometimes it can still return 503 HTTP status, that means deploying was complete although
the server is still booting. So you need just to wait a bit.

<div class="admonition note">
<p class="admonition-title">Note</p>
<p>See details about the <code>amsdal cloud deploys</code> command here: <a href="/cli/api/cli/#amsdal-cloud-cld-deploy">AMSDAL CLI - deploy</a></p>
</div>